In [ ]:
from google.colab import drive
import sys
from pathlib import Path

drive.mount("/content/drive", force_remount = True)


Mounted at /content/drive


In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

import tensorflow as tf
from tensorflow.keras.models import *  # Import the whole module
from tensorflow.keras.layers import *
from tensorflow.keras.callbacks import *
from tensorflow.keras.optimizers import *
from tensorflow.keras.applications import VGG16
from tensorflow.keras.applications.vgg16 import preprocess_input
from tensorflow.keras.preprocessing.image import ImageDataGenerator

import cv2  # To work with images
import random
import itertools  # To work with iterations
import os  # To work with the operating system, such as folders, files, ...

from sklearn.metrics import confusion_matrix, accuracy_score, silhouette_score
from sklearn.cluster import KMeans

In [ ]:
### DEFINE SOME PARAMETERS ###

base_path = "/content/drive/My Drive/LapSync/21Apr/"
SHAPE = (224,224,3)
batch_size = 256

In [ ]:
### MODEL FUNCTION ###

def get_model(train=True):
    
    pre_process = Lambda(preprocess_input)
    vgg = VGG16(weights = 'imagenet', include_top = True, input_shape = SHAPE)
    vgg = Model(vgg.input, vgg.layers[-3].output)
    vgg.trainable = False
    
    inp = Input(SHAPE)
    vgg_16_process = pre_process(GaussianNoise(0.1)(inp))
    vgg_out = vgg(vgg_16_process)
    
    if train:
        x = Lambda(lambda z: tf.concat(z, axis=0))([vgg_out,noise])
        x = Activation('relu')(x)
    else:
        x = vgg_out
        
    out = x

    model = Model(inp, out)
    model.compile(Adam(lr=1e-4), loss='binary_crossentropy')
    
    return model

In [ ]:
### SWITCH TO INFERENCE MODE TO COMPUTE PREDICTIONS ###

ineference_model = get_model(train=False)


/usr/local/lib/python3.7/dist-packages/tensorflow/python/keras/optimizer_v2/optimizer_v2.py:375: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  "The `lr` argument is deprecated, use `learning_rate` instead.")


In [ ]:
import collections
odtest_datagen = ImageDataGenerator()
odtest_generator = odtest_datagen.flow_from_directory(
            '/content/drive/My Drive/LapSync/21Apr/Exper3/length17/',
            target_size = (SHAPE[0], SHAPE[1]),
            batch_size = 1,
            class_mode = 'categorical',
            shuffle = False,
            seed = 33,
            classes = ['2digit']
)
pred_TEST = ineference_model.predict(odtest_generator)
kmeans = KMeans(n_clusters = 3, random_state = 0).fit(pred_TEST)
nTEST = kmeans.predict(pred_TEST)
#print(collections.Counter(nTEST))

from scipy.io import savemat
mdic = {"nTEST": nTEST}
#savemat('/content/drive/My Drive/LapSync/21Apr/21Apr/pred_corr.mat', mdic)

Found 90 images belonging to 1 classes.


In [ ]:
nTEST

array([0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 2, 2, 2, 2, 2, 2,
       2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0], dtype=int32)

In [ ]:
odtest_datagen1 = ImageDataGenerator()
odtest_datagen2 = ImageDataGenerator()
odtest_datagen3 = ImageDataGenerator()

odtest_generator1 = odtest_datagen1.flow_from_directory(
            '/content/drive/My Drive/LapSync/21Apr/Exper3/length17/',
            target_size = (SHAPE[0], SHAPE[1]),
            batch_size = 1,
            class_mode = 'categorical',
            shuffle = False,
            seed = 33,
            classes = ['1digit']
)

odtest_generator2 = odtest_datagen2.flow_from_directory(
            '/content/drive/My Drive/LapSync/21Apr/Exper3/length17/',
            target_size = (SHAPE[0], SHAPE[1]),
            batch_size = 1,
            class_mode = 'categorical',
            shuffle = False,
            seed = 33,
            classes = ['2digit']
)

odtest_generator3 = odtest_datagen3.flow_from_directory(
            '/content/drive/My Drive/LapSync/21Apr/Exper3/length17/',
            target_size = (SHAPE[0], SHAPE[1]),
            batch_size = 1,
            class_mode = 'categorical',
            shuffle = False,
            seed = 33,
            classes = ['3digit']
)

pred_TEST1 = ineference_model.predict(odtest_generator1)
pred_TEST2 = ineference_model.predict(odtest_generator2)
pred_TEST3 = ineference_model.predict(odtest_generator3)

nTEST1 = kmeans.predict(pred_TEST1)
nTEST2 = kmeans.predict(pred_TEST2)
nTEST3 = kmeans.predict(pred_TEST3)

#print(collections.Counter(nTEST2))
from scipy.io import savemat
mdic1 = {"nTEST1": nTEST1}
mdic2 = {"nTEST2": nTEST2}
mdic3 = {"nTEST3": nTEST3}

savemat('/content/drive/My Drive/LapSync/21Apr/Exper3/pred1.mat', mdic1)
savemat('/content/drive/My Drive/LapSync/21Apr/Exper3/pred2.mat', mdic2)
savemat('/content/drive/My Drive/LapSync/21Apr/Exper3/pred3.mat', mdic3)

Found 10 images belonging to 1 classes.
Found 90 images belonging to 1 classes.
Found 294 images belonging to 1 classes.


In [ ]:
nTEST1

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [ ]:
nTEST2

array([0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 2, 2, 2, 2, 2, 2,
       2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0], dtype=int32)

In [ ]:
nTEST3

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       2, 2, 1, 1, 1, 1, 1, 2, 2, 2, 2, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)